In [3]:
import pandas as pd
from dotenv import load_dotenv
from fastapi import FastAPI
import pyodbc
import os

load_dotenv('.env')

server = os.getenv('SERVER')
database = os.getenv('DATABASE')
username = os.getenv('USERNAME')
password = os.getenv('PASSWORD')
driver = os.getenv('DRIVER')

connection_string = f"DRIVER={driver};SERVER={server};DATABASE={database};UID={username};PWD={password};TrustServerCertificate=Yes"
conn = pyodbc.connect(connection_string)
cursor = conn.cursor()

In [67]:
query = '''
            SELECT
            	    Equipamento.Descricao AS descricaoEquipamento
            	    , InstalacaoEletrica.Descricao AS descricaoInstalacaoEletrica
            	    , gc.Descricao AS GrupoDeCalculo
            	    , Calculo.Codigo AS CodigoCalculo
            	    , Calculo.Descricao AS DescricaoCalculo
            	    , ExecucaoCalculoResultado.Resultado AS HI
            		, MIN(CAST(ExecucaoCalculoResultado.UltimaAtualizacao AS DATE)) AS PeriodoHIInicio
            		, MAX(CAST(ExecucaoCalculoResultado.UltimaAtualizacao AS DATE)) AS PeriodoHIFim
            	FROM EngineCalculo.CalculoResultado As ExecucaoCalculoResultado
            	INNER JOIN EngineCalculo.CalculoResultadoEquipamento 
            		ON CalculoResultadoEquipamento.CalculoId = ExecucaoCalculoResultado.CalculoId 
            	    AND CalculoResultadoEquipamento.JobId = ExecucaoCalculoResultado.JobId
            	INNER JOIN EngineCalculo.Calculo
            		ON Calculo.Id = ExecucaoCalculoResultado.CalculoId
            	INNER JOIN EngineCalculo.CalculoResultadoVariavel As EntradaVariavel 
            		ON ExecucaoCalculoResultado.JobId = EntradaVariavel.JobId
            	INNER JOIN EngineCalculo.RevisaoVariavel As RevisaoVariavel 
            	    ON RevisaoVariavel.VariavelId = EntradaVariavel.VariavelId 
            		AND RevisaoVariavel.Revisao = EntradaVariavel.Revisao
            	INNER JOIN Equipamento
            		ON Equipamento.Id = CalculoResultadoEquipamento.EquipamentoId
            	INNER JOIN EquipamentoInstalacaoEletrica AS eie
            		ON eie.EquipamentoId = Equipamento.Id
            	INNER JOIN InstalacaoEletrica AS InstalacaoEletrica
            		ON InstalacaoEletrica.Id = eie.InstalacaoEletricaId
            	INNER JOIN EngineCalculo.GrupoCalculo AS gc
            		ON gc.Id = Calculo.GrupoCalculoId
            	WHERE 
            		Calculo.Codigo IN ('IE_TR' ,'I2_TR')
            	    AND ExecucaoCalculoResultado.UltimaAtualizacao >= '2023-06-16'
            	    AND ExecucaoCalculoResultado.UltimaAtualizacao <= '2023-07-31'
            		AND Equipamento.Id = 136
            	GROUP BY 
            	    Equipamento.Descricao
            	    , InstalacaoEletrica.Descricao
            	    , gc.Descricao
            	    , Calculo.Codigo
            	    , Calculo.Descricao
            	    , ExecucaoCalculoResultado.Resultado
            	ORDER BY 
            		Calculo.Descricao DESC
            		, PeriodoHIFim DESC
            		, PeriodoHIInicio DESC
                    '''
resultado = cursor.execute(query)
registro = resultado.fetchall()
colunas = [column[0] for column in cursor.description]
data = [dict(zip(colunas, row)) for row in registro]
data

[{'descricaoEquipamento': 'Reator CORE7-06 Fase B',
  'descricaoInstalacaoEletrica': 'Colinas',
  'GrupoDeCalculo': 'Índice de Impacto do Equipamento',
  'CodigoCalculo': 'I2_TR',
  'DescricaoCalculo': 'Índice de Impacto do Equipamento',
  'HI': 0.188561507936508,
  'PeriodoHIInicio': datetime.date(2023, 6, 16),
  'PeriodoHIFim': datetime.date(2023, 7, 7)},
 {'descricaoEquipamento': 'Reator CORE7-06 Fase B',
  'descricaoInstalacaoEletrica': 'Colinas',
  'GrupoDeCalculo': 'Health Index do Equipamento',
  'CodigoCalculo': 'IE_TR',
  'DescricaoCalculo': 'Índice de Estado do Equipamento',
  'HI': 1.0,
  'PeriodoHIInicio': datetime.date(2023, 6, 17),
  'PeriodoHIFim': datetime.date(2023, 7, 7)},
 {'descricaoEquipamento': 'Reator CORE7-06 Fase B',
  'descricaoInstalacaoEletrica': 'Colinas',
  'GrupoDeCalculo': 'Health Index do Equipamento',
  'CodigoCalculo': 'IE_TR',
  'DescricaoCalculo': 'Índice de Estado do Equipamento',
  'HI': 2.0,
  'PeriodoHIInicio': datetime.date(2023, 6, 16),
  'Per

In [8]:
query = '''
            SELECT 
    oe.TipoObjeto AS TipoOjeto
    , oe.IdentificadorEcm AS IdentificadorModulo
    , oe.Descricao
	, ove.IdentificadorEcm
	, ove.Codigo
	, ove.Descricao
FROM EngineCalculo.ObjetoEcm AS oe
INNER JOIN EngineCalculo.ObjetoVariavelEcm AS ove 
	ON ove.ObjetoId = oe.Id 
WHERE ove.Ativo = 1
ORDER BY oe.TipoObjeto
		, oe.IdentificadorEcm 
		, ove.IdentificadorEcm
                '''
resultado = cursor.execute(query)
registro = resultado.fetchall()
colunas = [column[0] for column in cursor.description]
data = [dict(zip(colunas, row)) for row in registro]
df_2 = pd.DataFrame(data)
df_2[df_2['IdentificadorModulo'] == 194].head(50)

TipoOjeto  IdentificadorModulo  \
2453          2                  194   
2454          2                  194   
2455          2                  194   
2456          2                  194   
2457          2                  194   
2458          2                  194   
2459          2                  194   
2460          2                  194   
2461          2                  194   
2462          2                  194   
2463          2                  194   
3441          3                  194   
3442          3                  194   
3443          3                  194   
3444          3                  194   
3445          3                  194   
3446          3                  194   
3447          3                  194   
3448          3                  194   
3449          3                  194   
3450          3                  194   
3451          3                  194   
3452          3                  194   
3453          3                  194   
3454          3                  194   
3455          3                  194   
3456          3                  194   
3457          3                  194   
3458          3                  194   
3459          3                  194   
3460          3                  194   
3461          3                  194   
3462          3                  194   
3463          3                  194   
3464          3                  194   

                                              Descricao  IdentificadorEcm  \
2453                                    H2 - Hidrogênio              8492   
2454                                       CH4 - Metano              8493   
2455                                       C2H6 - Etano              8494   
2456                                     C2H4 - Etileno              8495   
2457                                   C2H2 - Acetileno              8496   
2458                           CO - Monóxido de Carbono              8497   
2459                           CO2 - Dióxido de Carbono              8498   
2460                                    N2 - Nitrogênio              8499   
2461                                       O2 -Oxigênio              8500   
2462                       Limite de detecção analítica              8501   
2463                      Taxa de aumento de H2 no óleo              8805   
3441    Cromatografia - D2 - Descargas de alta energia.               974   
3442  Cromatografia - Descargas parciais com baixa d...               975   
3443  Cromatografia - Descargas parciais com alta de...               976   
3444         Cromatografia - Descargas de baixa energia               977   
3445          Cromatografia - Descargas de alta energia               978   
3446  Cromatografia - Falta térmica de baixa tempera...               979   
3447  Cromatografia - Falta térmica de baixa tempera...               980   
3448  Cromatografia - Falta térmica de média tempera...               981   
3449  Cromatografia - Falta térmica de alta temperat...               982   
3450           Cromatografia - PD - Descargas parciais.               983   
3451   Cromatografia - D1 - Descargas de baixa energia.               984   
3452     Cromatografia - T1 - Falta térmica, t < 300ºC.               985   
3453    Cromatografia - D2 - Descargas de alta energia.               986   
3454  Cromatografia - T2 - Falta térmica, 300 ºC < t...               987   
3455     Cromatografia - T3 - Falta térmica, t > 700 ºC               988   
3456           Cromatografia - PD - Descargas parciais.               989   
3457   Cromatografia - D1 - Descargas de baixa energia.               990   
3458    Cromatografia - D2 - Descargas de alta energia.               991   
3459     Cromatografia - T1 - Falta térmica, t < 300ºC.               992   
3460  Cromatografia - T2 - Falta térmica, 300 ºC < t...               993   
3461    Cromatografia - T3 - Falta térmica, t > 700 ºC.               994   
3462  Cromatografia - D+

In [156]:
SUBSYSTE_PARAMS = [
      {"nome": "Capacitância 1", "subsistema": "Bucha", "identificador": 2070},
      {"nome": "Capacitância 2", "subsistema": "Bucha", "identificador": 2071},
      {"nome": "Capacitância 3", "subsistema": "Bucha","identificador": 2072},
      {"nome": "Tendência de evolução da Capacitância 1", "subsistema": "Bucha", "identificador": 2073},
      {"nome": "Tendência de evolução da Capacitância 2", "subsistema": "Bucha", "identificador": 2074},
      {"nome": "Tendência de evolução da Capacitância 3", "subsistema": "Bucha", "identificador": 2075},
      {"nome": "Tangente Delta, identificador 1", "subsistema": "Bucha", "identificador": 2076},
      {"nome": "Tangente Delta, identificador 2", "subsistema": "Bucha", "identificador": 2077},
      {"nome": "Tangente Delta, identificador 3", "subsistema": "Bucha", "identificador": 2078},
      {"nome": "Tendência de evolução da Tangente Delta 1", "subsistema": "Bucha", "identificador": 2079},
      {"nome": "Tendência de evolução da Tangente Delta 2", "subsistema": "Bucha","identificador": 2080},
      {"nome": "Tendência de evolução da Tangente Delta 3", "subsistema": "Bucha", "identificador": 2081},
      {"nome": "Corrente de Fuga, identificador 1", "subsistema": "Bucha","identificador": 2097},
      {"nome": "Corrente de Fuga, identificador 2", "subsistema": "Bucha","identificador": 2098},
      {"nome": "Corrente de Fuga, identificador 3", "subsistema": "Bucha","identificador": 2099},
      {"nome": "Somatória das Correntes de Fuga - BT (baixa tensão)", "subsistema": "Bucha","identificador": 2187},
      {"nome": "Ângulo da Somatória das Correntes - BT (baixa tensão)", "subsistema": "Bucha","identificador": 2209},
      {"nome": "Ângulo da Somatória das Correntes - MT (média tensão)", "subsistema": "Bucha","identificador": 2823},
      {"nome": "Temperatura do Enrolamento 1", "subsistema": "Parte Ativa", "identificador": 2593},
      {"nome": "Temperatura do Enrolamento 2", "subsistema": "Parte Ativa","identificador": 2035},
      {"nome": "Temperatura do Enrolamento 3", "subsistema": "Parte Ativa","identificador": 2043},
      {"nome": "Umidade relativa do óleo", "subsistema": "Parte Ativa","identificador": 9710},
      {"nome": "Umidade do Papel do Enrolamento 1", "subsistema": "Parte Ativa","identificador": 11784},
      {"nome": "Umidade do Papel do Enrolamento 2", "subsistema": "Parte Ativa","identificador": 11787},
      {"nome": "Umidade do Papel do Enrolamento 3", "subsistema": "Parte Ativa","identificador": 11790},
      {"nome": "Corrente do enrolamento 1", "subsistema": "Parte Ativa","identificador": 11629},
      {"nome": "Corrente do enrolamento 2", "subsistema": "Parte Ativa","identificador": 11643},
      {"nome": "Corrente do enrolamento 3", "subsistema": "Parte Ativa","identificador": 11657},
      {"nome": "Hidrogênio dissolvido no óleo", "subsistema": "Parte Ativa","identificador": 2363},
      {"nome": "Tendência de evolução do hidrogênio", "subsistema": "Parte Ativa","identificador": 2364},
      {"nome": "H2 - Hidrogênio", "subsistema": "Parte Ativa","identificador": 8492},
      {"nome": "CH4 - Metano", "subsistema": "Parte Ativa","identificador": 8493},
      {"nome": "C2H6 - Etano","subsistema": "Parte Ativa", "identificador": 8494},
      {"nome": "C2H4 - Etileno", "subsistema": "Parte Ativa","identificador": 8495},
      {"nome": "C2H2 - Acetileno", "subsistema": "Parte Ativa","identificador": 8496},
      {"nome": "CO - Monóxido de Carbono", "subsistema": "Parte Ativa","identificador": 8497},
      {"nome": "CO2 - Dióxido de Carbono", "subsistema": "Parte Ativa","identificador": 8498},
      {"nome": "N2 - Nitrogênio","subsistema": "Parte Ativa", "identificador": 8499},
      {"nome": "O2 - Oxigênio", "subsistema": "Parte Ativa","identificador": 8500}
  ]

In [157]:
from datetime import datetime, timedelta

def gerar_datas_intervalo(data_inicial, data_final):
    # Converter as strings de data em objetos datetime
    data_inicial = datetime.strptime(data_inicial, '%Y-%m-%dT%H:%M:%S')
    data_final = datetime.strptime(data_final, '%Y-%m-%dT%H:%M:%S')

    # Inicializar a lista que irá armazenar as datas do intervalo
    datas_intervalo = []

    # Loop para gerar as datas no intervalo
    data_atual = data_inicial
    while data_atual <= data_final:
        datas_intervalo.append(data_atual.strftime('%Y-%m-%dT%H:%M:%S'))
        data_atual += timedelta(days=1)

    return datas_intervalo

# Exemplo de uso da função
data_inicio = '2023-08-01T00:00:00'
data_fim = '2023-08-06T23:59:59'
intervalo_de_datas = gerar_datas_intervalo(data_inicio, data_fim)
print(intervalo_de_datas)


['2023-08-01T00:00:00', '2023-08-02T00:00:00', '2023-08-03T00:00:00', '2023-08-04T00:00:00', '2023-08-05T00:00:00', '2023-08-06T00:00:00']


In [167]:
from src.ecm.ECM import ECM
import datetime


ecm = ECM()
data = ecm.request_results(datetime.datetime.now().strftime('%Y-%m-%dT%H:%M:%S'), datetime.datetime.now().strftime('%Y-%m-%dT%H:%M:%S'), 30)

response<Response [200]>


In [168]:
data

[{'equipamentoSigmaId': 30,
  'tipoObjetos': [{'tipoObjeto': 4,
    'objetos': [{'identificador': 101,
      'variaveis': [{'identificador': 1,
        'codigo': 'StatusDevice',
        'valor': '3',
        'dataMedicao': '2022-06-06T02:04:08.767Z',
        'tipoRetorno': 1},
       {'identificador': 2,
        'codigo': 'Autodiag',
        'valor': '0',
        'dataMedicao': '2022-06-06T02:04:08.767Z',
        'tipoRetorno': 1}]},
     {'identificador': 102,
      'variaveis': [{'identificador': 1,
        'codigo': 'StatusDevice',
        'valor': '3',
        'dataMedicao': '2022-06-06T02:04:08.787Z',
        'tipoRetorno': 1},
       {'identificador': 2,
        'codigo': 'Autodiag',
        'valor': '0',
        'dataMedicao': '2022-06-06T02:04:08.787Z',
        'tipoRetorno': 1}]},
     {'identificador': 103,
      'variaveis': [{'identificador': 1,
        'codigo': 'StatusDevice',
        'valor': '3',
        'dataMedicao': '2022-06-06T02:04:08.807Z',
        'tipoRetorno': 

In [159]:
ecm_list = []
for time in intervalo_de_datas:
    data = ecm.request_results(time,
                               time, 
                                int(df.EquipamentoSigmaId.values[0]))
    ecm_list.append(data)

response<Response [200]>
response<Response [200]>
response<Response [200]>
response<Response [200]>
response<Response [200]>
response<Response [200]>


In [166]:
ecm_list

[[{'equipamentoSigmaId': 30,
   'tipoObjetos': [{'tipoObjeto': 4,
     'objetos': [{'identificador': 101,
       'variaveis': [{'identificador': 1,
         'codigo': 'StatusDevice',
         'valor': '3',
         'dataMedicao': '2022-06-06T02:04:08.767Z',
         'tipoRetorno': 1},
        {'identificador': 2,
         'codigo': 'Autodiag',
         'valor': '0',
         'dataMedicao': '2022-06-06T02:04:08.767Z',
         'tipoRetorno': 1}]},
      {'identificador': 102,
       'variaveis': [{'identificador': 1,
         'codigo': 'StatusDevice',
         'valor': '3',
         'dataMedicao': '2022-06-06T02:04:08.787Z',
         'tipoRetorno': 1},
        {'identificador': 2,
         'codigo': 'Autodiag',
         'valor': '0',
         'dataMedicao': '2022-06-06T02:04:08.787Z',
         'tipoRetorno': 1}]},
      {'identificador': 103,
       'variaveis': [{'identificador': 1,
         'codigo': 'StatusDevice',
         'valor': '3',
         'dataMedicao': '2022-06-06T02:04:08.8

In [165]:
SUBSYSTE_PARAMS = [
      {"nome": "Capacitância 1", "subsistema": "Bucha", "identificador": 2070},
      {"nome": "Capacitância 2", "subsistema": "Bucha", "identificador": 2071},
      {"nome": "Capacitância 3", "subsistema": "Bucha","identificador": 2072},
      {"nome": "Tendência de evolução da Capacitância 1", "subsistema": "Bucha", "identificador": 2073},
      {"nome": "Tendência de evolução da Capacitância 2", "subsistema": "Bucha", "identificador": 2074},
      {"nome": "Tendência de evolução da Capacitância 3", "subsistema": "Bucha", "identificador": 2075},
      {"nome": "Tangente Delta, identificador 1", "subsistema": "Bucha", "identificador": 2076},
      {"nome": "Tangente Delta, identificador 2", "subsistema": "Bucha", "identificador": 2077},
      {"nome": "Tangente Delta, identificador 3", "subsistema": "Bucha", "identificador": 2078},
      {"nome": "Tendência de evolução da Tangente Delta 1", "subsistema": "Bucha", "identificador": 2079},
      {"nome": "Tendência de evolução da Tangente Delta 2", "subsistema": "Bucha","identificador": 2080},
      {"nome": "Tendência de evolução da Tangente Delta 3", "subsistema": "Bucha", "identificador": 2081},
      {"nome": "Corrente de Fuga, identificador 1", "subsistema": "Bucha","identificador": 2097},
      {"nome": "Corrente de Fuga, identificador 2", "subsistema": "Bucha","identificador": 2098},
      {"nome": "Corrente de Fuga, identificador 3", "subsistema": "Bucha","identificador": 2099},
      {"nome": "Somatória das Correntes de Fuga - BT (baixa tensão)", "subsistema": "Bucha","identificador": 2187},
      {"nome": "Ângulo da Somatória das Correntes - BT (baixa tensão)", "subsistema": "Bucha","identificador": 2209},
      {"nome": "Ângulo da Somatória das Correntes - MT (média tensão)", "subsistema": "Bucha","identificador": 2823},
      {"nome": "Temperatura do Enrolamento 1", "subsistema": "Parte Ativa", "identificador": 2593},
      {"nome": "Temperatura do Enrolamento 2", "subsistema": "Parte Ativa","identificador": 2035},
      {"nome": "Temperatura do Enrolamento 3", "subsistema": "Parte Ativa","identificador": 2043},
      {"nome": "Umidade relativa do óleo", "subsistema": "Parte Ativa","identificador": 9710},
      {"nome": "Umidade do Papel do Enrolamento 1", "subsistema": "Parte Ativa","identificador": 11784},
      {"nome": "Umidade do Papel do Enrolamento 2", "subsistema": "Parte Ativa","identificador": 11787},
      {"nome": "Umidade do Papel do Enrolamento 3", "subsistema": "Parte Ativa","identificador": 11790},
      {"nome": "Corrente do enrolamento 1", "subsistema": "Parte Ativa","identificador": 11629},
      {"nome": "Corrente do enrolamento 2", "subsistema": "Parte Ativa","identificador": 11643},
      {"nome": "Corrente do enrolamento 3", "subsistema": "Parte Ativa","identificador": 11657},
      {"nome": "Hidrogênio dissolvido no óleo", "subsistema": "Parte Ativa","identificador": 2363},
      {"nome": "Tendência de evolução do hidrogênio", "subsistema": "Parte Ativa","identificador": 2364},
      {"nome": "H2 - Hidrogênio", "subsistema": "Parte Ativa","identificador": 8492},
      {"nome": "CH4 - Metano", "subsistema": "Parte Ativa","identificador": 8493},
      {"nome": "C2H6 - Etano","subsistema": "Parte Ativa", "identificador": 8494},
      {"nome": "C2H4 - Etileno", "subsistema": "Parte Ativa","identificador": 8495},
      {"nome": "C2H2 - Acetileno", "subsistema": "Parte Ativa","identificador": 8496},
      {"nome": "CO - Monóxido de Carbono", "subsistema": "Parte Ativa","identificador": 8497},
      {"nome": "CO2 - Dióxido de Carbono", "subsistema": "Parte Ativa","identificador": 8498},
      {"nome": "N2 - Nitrogênio","subsistema": "Parte Ativa", "identificador": 8499},
      {"nome": "O2 - Oxigênio", "subsistema": "Parte Ativa","identificador": 8500}
  ]
teste = []
for entry in ecm_list:
    for params in entry:
        if isinstance(params['tipoObjetos'], list):
            for typeObject in params['tipoObjetos']:
                for data_objetos in typeObject['objetos']:
                        for variavel in data_objetos['variaveis']:
                            for subsystem in SUBSYSTE_PARAMS:
                                if variavel['identificador'] == subsystem['identificador'] and 'valor' in variavel and 'Bucha' in subsystem['subsistema']:
                                    teste.append({
                                        "identificador": variavel['identificador'],
                                        "codigo": variavel['codigo'],
                                        "subsistema": "Bucha",
                                        "valor": variavel['valor'],
                                        "dataMedicao": variavel['dataMedicao'],
                                        "tipoRetorno": variavel['tipoRetorno'],
                                        "nome": subsystem['nome'],
                                    })
                                elif variavel['identificador'] == subsystem['identificador'] and 'valor' in variavel and 'Parte Ativa' in subsystem['subsistema']:
                                    teste.append({
                                                "identificador": variavel['identificador'],
                                                "codigo": variavel['codigo'],
                                                "subsistema": "Parte Ativa",
                                                "valor": variavel['valor'],
                                                "dataMedicao": variavel['dataMedicao'],
                                                "tipoRetorno": variavel['tipoRetorno'],
                                                "nome": subsystem['nome'],
                                            })
teste

[{'identificador': 2035,
  'codigo': 'Get_TemperatureWinding2',
  'subsistema': 'Parte Ativa',
  'valor': '65,5',
  'dataMedicao': '2022-08-17T12:16:10.707Z',
  'tipoRetorno': 1,
  'nome': 'Temperatura do Enrolamento 2'},
 {'identificador': 2043,
  'codigo': 'Get_TemperatureWinding3',
  'subsistema': 'Parte Ativa',
  'valor': '64,1',
  'dataMedicao': '2022-08-17T12:16:10.707Z',
  'tipoRetorno': 1,
  'nome': 'Temperatura do Enrolamento 3'},
 {'identificador': 2070,
  'codigo': 'Get_FA_Capacitance',
  'subsistema': 'Bucha',
  'valor': '541,5',
  'dataMedicao': '2022-08-17T12:16:10.707Z',
  'tipoRetorno': 1,
  'nome': 'Capacitância 1'},
 {'identificador': 2071,
  'codigo': 'Get_FB_Capacitance',
  'subsistema': 'Bucha',
  'valor': '540',
  'dataMedicao': '2022-08-17T12:16:10.707Z',
  'tipoRetorno': 1,
  'nome': 'Capacitância 2'},
 {'identificador': 2073,
  'codigo': 'Get_FA_CapacitanceTrend',
  'subsistema': 'Bucha',
  'valor': '0',
  'dataMedicao': '2022-08-17T12:16:10.707Z',
  'tipoRetor

In [161]:
def extract_identifiers(data):
    identifiers = []

    for entry in ecm_list:
            for typeObject in entry['tipoObjetos']:
                for data_objetos in typeObject['objetos']:
                    for variavel in data_objetos['variaveis']:
                        for subsystem in SUBSYSTE_PARAMS:
                            if variavel['identificador'] == subsystem['identificador'] and 'valor' in variavel and 'Bucha' in subsystem['subsistema']:
                                identifiers.append({
                                    "identificador": variavel['identificador'],
                                    "codigo": variavel['codigo'],
                                    "subsistema": "Bucha",
                                    "valor": variavel['valor'],
                                    "dataMedicao": variavel['dataMedicao'],
                                    "tipoRetorno": variavel['tipoRetorno'],
                                    "nome": subsystem['nome'],
                                })
                            elif variavel['identificador'] == subsystem['identificador'] and 'valor' in variavel and 'Parte Ativa' in subsystem['subsistema']:
                                identifiers.append({
                                            "identificador": variavel['identificador'],
                                            "codigo": variavel['codigo'],
                                            "subsistema": "Parte Ativa",
                                            "valor": variavel['valor'],
                                            "dataMedicao": variavel['dataMedicao'],
                                            "tipoRetorno": variavel['tipoRetorno'],
                                            "nome": subsystem['nome'],
                                        })

    return identifiers

identifiers_array = extract_identifiers(data)

NameError: name 'data_params' is not defined

In [8]:
new_data = []
for info in data:
    new_data.append(
        {
            "R": info['R'],
            "F": info['F'],
            "t": info["t"],
            "faultness": info['R']
        }
    )

In [21]:
import numpy as np
import datetime

def calculate_probabilities(data, defect_rate = [1e-5*40,
                                                 1e-5*40,
                                                 1e-5*40,
                                                 1e-5*40], 
                                                 failure_rate = 1e-5,
                                                 data_entrada_operação = "01-01-2003"):
                                                 
    # defect rate em dias
    actual_state = data["HealtIndex"].iloc[-1]
    defect_rate = defect_rate[actual_state-1]

    data["HealtIndex"] -=  actual_state
    if (data["HealtIndex"] > 0).sum() == 0:
        data_state = data["UltimaAtualizacaoCalculo"].iloc[0]
    else:
        data_state = data[data["HealtIndex"] == 1].iloc[0]["UltimaAtualizacaoCalculo"]
    
    data_diff = (datetime.datetime.today() - pd.to_datetime(data_state)).days
    data_failure_diff = datetime.datetime.today() - pd.to_datetime(data_entrada_operação)
    data_failure_diff = data_failure_diff.days

    failure_probability = 1-np.exp((-failure_rate*data_failure_diff))

    #FIXME consertar a probabilidade de transição de estado # implementar aqui markov 
    if actual_state == 1:
        state_probability = 1-np.exp((-defect_rate*data_failure_diff)) + failure_probability
    else:
        state_probability = 1-np.exp((-defect_rate*data_diff)) + failure_probability

    if state_probability > 1:
        state_probability = 1
    if failure_probability > 1:
        failure_probability = 1
    

    return {"probabilidade_proximo_estado_equipamento": state_probability,
            "Probabilidade_proximo_estado_bucha": state_probability*0.3,
            "Probabilidade_proximo_estado_ativa": state_probability*0.7,
            "probabilidade_falha_equipamento": failure_probability,
            "Probabilidade_falha_bucha": failure_probability*0.3,
            "Probabilidade_falha_ativa": failure_probability*0.7
            }